<a href="https://colab.research.google.com/github/Avipsa1/UPPP275-Notebooks/blob/main/Creating_Heatmap_using_Folium.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Initialize a folium map
You can find additional leaflet basemap tiles here: http://leaflet-extras.github.io/leaflet-providers/preview

In [1]:
import folium
boston = [42.3202, -71.1500]
map = folium.Map(
    location = boston,
    zoom_start = 11,
    tiles = 'https://{s}.tile.opentopomap.org/{z}/{x}/{y}.png',
    attr = 'Map data: &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors, <a href="http://viewfinderpanoramas.org">SRTM</a> | Map style: &copy; <a href="https://opentopomap.org">OpenTopoMap</a> (<a href="https://creativecommons.org/licenses/by-sa/3.0/">CC-BY-SA</a>)'
)
map

Read crime data in a pandas dataframe

In [2]:
import pandas as pd
crimes = pd.read_csv("boston_crime.csv",encoding= 'unicode_escape')

Access dataframe values

In [3]:
crimes.head()

INCIDENT_NUMBER  OFFENSE_CODE    OFFENSE_CODE_GROUP   OFFENSE_DESCRIPTION  \
0      I182070945           619               Larceny    LARCENY ALL OTHERS   
1      I182070943          1402             Vandalism             VANDALISM   
2      I182070941          3410                 Towed   TOWED MOTOR VEHICLE   
3      I182070940          3114  Investigate Property  INVESTIGATE PROPERTY   
4      I182070938          3114  Investigate Property  INVESTIGATE PROPERTY   

  DISTRICT REPORTING_AREA SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH  \
0      D14            808      NaN  2018-09-02 13:00:00  2018      9   
1      C11            347      NaN  2018-08-21 00:00:00  2018      8   
2       D4            151      NaN  2018-09-03 19:27:00  2018      9   
3       D4            272      NaN  2018-09-03 21:16:00  2018      9   
4       B3            421      NaN  2018-09-03 21:05:00  2018      9   

  DAY_OF_WEEK  HOUR    UCR_PART       STREET        Lat       Long  \
0      Sunday    13    Part One   LINCOLN ST  42.357791 -71.139371   
1     Tuesday     0    Part Two     HECLA ST  42.306821 -71.060300   
2      Monday    19  Part Three  CAZENOVE ST  42.346589 -71.072429   
3      Monday    21  Part Three   NEWCOMB ST  42.334182 -71.078664   
4      Monday    21  Part Three     DELHI ST  42.275365 -71.090361   

                      Location  
0  (42.35779134, -71.13937053)  
1  (42.30682138, -71.06030035)  
2  (42.34658879, -71.07242943)  
3  (42.33418175, -71.07866441)  
4  (42.27536542, -71.09036101)

In [6]:
crimes.DISTRICT.value_counts()

B2     49945
C11    42530
D4     41915
A1     35717
B3     35442
C6     23460
D14    20127
E13    17536
E18    17348
A7     13544
E5     13239
A15     6505
Name: DISTRICT, dtype: int64

Rename or drop unwanted columns

In [7]:
renamed_columns = {
    'OCCURRED_ON_DATE': 'date',
    'OFFENSE_CODE_GROUP': 'offense',
    'SHOOTING': 'shooting',
    'Lat': 'lat',
    'Long': 'lon'
}
crimes = crimes.rename(columns = renamed_columns)
crimes = crimes[list(renamed_columns.values())]

In [8]:
crimes.columns

Index(['date', 'offense', 'shooting', 'lat', 'lon'], dtype='object')

Deal with different data types

In [9]:
#Convert date from String to timestamp format
crimes.date = pd.to_datetime(crimes.date)
#Sort the dataframe by date of occurrence of the crimes
crimes = crimes.sort_values(by = "date")
#Print the first 10 crime incidents from the sorted dataframe
crimes.date[0:10]

129056   2015-06-15 00:00:00
314676   2015-06-15 00:00:00
310350   2015-06-15 00:00:00
253464   2015-06-15 00:00:00
8793     2015-06-15 00:00:00
318414   2015-06-15 00:00:00
317446   2015-06-15 00:00:00
303001   2015-06-15 00:00:00
317447   2015-06-15 00:00:00
318621   2015-06-15 00:01:00
Name: date, dtype: datetime64[ns]

Deal with null values

In [10]:
crimes.shooting

129056    NaN
314676    NaN
310350    NaN
253464    NaN
8793      NaN
         ... 
8         NaN
4         NaN
5         NaN
3         NaN
6         NaN
Name: shooting, Length: 319073, dtype: object

In [11]:
crimes.shooting = (crimes.shooting == 'Y')
crimes = crimes.dropna()
crimes.head()

date           offense  shooting        lat        lon
129056 2015-06-15        Harassment     False  42.291093 -71.065945
314676 2015-06-15  Confidence Games     False  42.300217 -71.080979
310350 2015-06-15             Other     False  42.293606 -71.071887
253464 2015-06-15     Property Lost     False  42.283634 -71.082813
8793   2015-06-15     Property Lost     False  -1.000000  -1.000000

In [14]:
list(zip([-33.45], [-70.65]))

[(-33.45, -70.65)]

In [25]:
from folium.plugins import HeatMap

map1 = folium.Map(boston, zoom_start=11)
hmap = HeatMap(
    data = [[row['lat'],row['lon']] for index, row in crimes.iterrows()],
    radius = 10,
    min_opacity= 0.5
)
hmap.add_to(map1)
map1